In [4]:
%load_ext autoreload
%autoreload 2

In [5]:
import numpy as np
from timer import Timer
import pickle

In [6]:
neuronMax = 1
neuronMin = -1
neuronDtype = np.float32


class NeuralNetwork:
    @staticmethod
    def sigmoid(x, derivative=False):
        if derivative:
            return x * (1 - x)
        return 1 / (1 + np.exp(-x))

    @staticmethod
    def relu(x, derivative=False):
        if derivative:
            return 1.0 * (x > 0)
        return np.maximum(0, x)

    @staticmethod
    def leakyRelu(x, derivative=False):
        if derivative:
            return 1.0 * (x > 0) + 0.01 * (x <= 0)
        return np.maximum(0.01 * x, x)

    @staticmethod
    def absolute(x, derivative=False):
        if derivative:
            return 1 if x > 0 else -1
        return np.abs(x)


    # @staticmethod
    # def softmax(x):
    #     exps = np.exp(x - np.max(x))
    #     return exps / np.sum(exps, axis=1, keepdims=True)

    # @staticmethod
    # def softmaxDerivative(x):
    #     return x * (1 - x)
    @staticmethod
    def mseLoss(errorVector, derivative=False):
        if derivative:
            return errorVector
        return np.mean(np.square(errorVector))*0.5

    def __init__(self, layerSizes, activationFunctions):
        self.layerSizes = layerSizes
        self.activationFunctions = activationFunctions
        self.layers = [
            np.random.uniform(low=neuronMin, high=neuronMax, size=layerSizes[i]).astype(neuronDtype)
            for i in range(len(layerSizes))
        ]
        self.weights = [
            np.random.uniform(
                low=neuronMin, high=neuronMax, size=layerSizes[i] * layerSizes[i + 1]
            ).astype(neuronDtype).reshape(layerSizes[i], layerSizes[i + 1])
            for i in range(len(layerSizes) - 1)
        ]
        self.biases = [
            np.random.uniform(low=neuronMin, high=neuronMax, size=layerSizes[i + 1]).astype(
                neuronDtype
            )
            for i in range(len(layerSizes) - 1)
        ]

    def loadInput(self, input):
        self.layers[0] = input.astype(neuronDtype)

    def readOutput(self):
        return self.layers[-1]

    def forward(self):
        for i in range(len(self.weights)):
            self.layers[i + 1] = self.activationFunctions[i](
                np.dot(self.layers[i], self.weights[i]) + self.biases[i]
            )



    def backpropagation(self, target, learning_rate, lossFunction):
        output_error = lossFunction(target - self.layers[-1], derivative=True)

        for i in range(len(self.layers) - 2, -1, -1):
            # Calculate the derivative of the activation function
            derivative = self.activationFunctions[i](self.layers[i + 1], derivative=True)

            # Calculate the error of the current layer
            layer_error = np.dot(output_error * derivative, self.weights[i].T) * learning_rate

            # Calculate the adjustments for the weights and biases
            weight_adjustments = np.outer(self.layers[i], output_error)
            bias_adjustments = output_error

            # Update the weights and biases
            self.weights[i] += weight_adjustments * learning_rate
            self.biases[i] += bias_adjustments * learning_rate

            # Set the output error for the next iteration
            # np.normalize(layer_error)
            output_error = layer_error


In [25]:
x = NeuralNetwork([5_000, 40, 40, 169], [NeuralNetwork.leakyRelu, NeuralNetwork.leakyRelu, NeuralNetwork.leakyRelu])
nnTimer = Timer(precision=3)
# target = np.arange(169).astype(neuronDtype)
target = np.random.uniform(low = -1000, high = 1000, size = 169)
input = np.random.uniform(low = 0, high = 1, size = 5_000)

In [27]:
x.loadInput(input)
x.forward()
print(x.readOutput())

[-1.9085069e+00 -5.2538484e-01 -1.6587623e+00  4.2203104e+02
  1.0536341e+02  2.8254645e+02 -1.0581131e+00 -2.2931240e+00
 -3.5409850e-01  1.1211489e+02 -5.7527202e-01  3.5671078e+01
 -2.2679896e+00  2.1207335e+02 -2.1022315e+00 -1.3700886e+00
  4.7526386e+01 -1.2958238e+00  2.5702515e+00  5.2877399e+01
  1.3905028e+02 -1.0339106e+00  8.5664719e+01 -2.0760548e+00
 -8.9483857e-01 -4.3863004e-01 -3.3524141e+00  1.0320798e+02
  7.7075066e+01  3.1079996e+02  8.1686716e+00 -2.5661975e-01
 -3.0735281e-01  1.4048778e+02 -1.1476797e+00 -2.1884069e+00
 -7.0870489e-01  2.1069958e+02  3.2655667e+02 -6.9785452e-01
  1.8112500e+02  1.1988889e+02  2.8330078e+02  1.1352879e+02
 -3.6748188e+00  2.3298181e+02  1.6579100e+02  9.7780014e+01
  1.3837096e+01  2.0542097e+02  4.4975643e+01  2.5879501e+02
 -1.5357980e-02 -1.1816356e+00  1.9928059e+01 -3.1829411e-01
 -3.2078402e+00 -3.6659367e+00  9.7669731e+01  1.1487451e+02
 -5.5919945e-01  2.8913013e+02 -9.9181399e-02 -6.5518588e-02
 -1.1069006e+00 -6.47783

In [28]:
# learning_rate = 0.00001
# for i in range(200):
#     nnTimer.tic()
#     x.loadInput(input)
#     x.forward()
#     x.backpropagation(target, learning_rate)
#     print(x.readOutput())
#     nnTimer.toc()
# nnTimer.stats()
learning_rate = 0.00001
for i in range(2000):
    nnTimer.tic()
    x.loadInput(input)
    x.forward()
    x.backpropagation(target, learning_rate, NeuralNetwork.mseLoss)
    print(x.readOutput(), NeuralNetwork.mseLoss(target - x.readOutput()))
    nnTimer.toc()
nnTimer.stats()

[-1.9085069e+00 -5.2538484e-01 -1.6587623e+00  4.2203104e+02
  1.0536341e+02  2.8254645e+02 -1.0581131e+00 -2.2931240e+00
 -3.5409850e-01  1.1211489e+02 -5.7527202e-01  3.5671078e+01
 -2.2679896e+00  2.1207335e+02 -2.1022315e+00 -1.3700886e+00
  4.7526386e+01 -1.2958238e+00  2.5702515e+00  5.2877399e+01
  1.3905028e+02 -1.0339106e+00  8.5664719e+01 -2.0760548e+00
 -8.9483857e-01 -4.3863004e-01 -3.3524141e+00  1.0320798e+02
  7.7075066e+01  3.1079996e+02  8.1686716e+00 -2.5661975e-01
 -3.0735281e-01  1.4048778e+02 -1.1476797e+00 -2.1884069e+00
 -7.0870489e-01  2.1069958e+02  3.2655667e+02 -6.9785452e-01
  1.8112500e+02  1.1988889e+02  2.8330078e+02  1.1352879e+02
 -3.6748188e+00  2.3298181e+02  1.6579100e+02  9.7780014e+01
  1.3837096e+01  2.0542097e+02  4.4975643e+01  2.5879501e+02
 -1.5357980e-02 -1.1816356e+00  1.9928059e+01 -3.1829411e-01
 -3.2078402e+00 -3.6659367e+00  9.7669731e+01  1.1487451e+02
 -5.5919945e-01  2.8913013e+02 -9.9181399e-02 -6.5518588e-02
 -1.1069006e+00 -6.47783

In [30]:
predictions = x.readOutput()
for i in range(len(predictions)):
    print(f"Prediction:     {predictions[i]},               Target:    {target[i]}, Iteration:    {i}")

mse = target - predictions
sq = sum(mse**2)/len(mse)
sq

Prediction:     489.0655517578125,               Target:    489.0655575898179, Iteration:    0
Prediction:     945.1607055664062,               Target:    945.160792262503, Iteration:    1
Prediction:     505.82366943359375,               Target:    505.8236787203841, Iteration:    2
Prediction:     -846.595703125,               Target:    -846.5983485289763, Iteration:    3
Prediction:     738.34814453125,               Target:    738.3481574633884, Iteration:    4
Prediction:     -685.873046875,               Target:    -685.8752063042117, Iteration:    5
Prediction:     -692.9302368164062,               Target:    -692.9323864606415, Iteration:    6
Prediction:     704.5389404296875,               Target:    704.5387970921429, Iteration:    7
Prediction:     180.6456756591797,               Target:    180.64567878765752, Iteration:    8
Prediction:     -180.58253479003906,               Target:    -180.5831834260141, Iteration:    9
Prediction:     -169.2980194091797,               

1.910039791203344e-06

In [14]:
import numpy as np

size = 5
padding = 3

a = np.zeros((size + padding * 2, size + padding * 2))

for i in range(padding, size + padding):
    for j in range(padding, size + padding):
        a[i, j] = i - padding + (j - padding) * 10

In [15]:
a

array([[ 0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0., 10., 20., 30., 40.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  1., 11., 21., 31., 41.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  2., 12., 22., 32., 42.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  3., 13., 23., 33., 43.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  4., 14., 24., 34., 44.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.]])